In [3]:
import json
import os
os.environ["LLAMA_CPP_LIB"] = "/home/brian/github/llama.cpp/libllama.so"
from llama_cpp import Llama, Completion, LlamaTokenizer

In [4]:
# let's translate the text of the first chapter
with open("../data/books/three_body/chapters/1.json", "r") as f:
    chapter_1_json = json.loads(f.read())


In [5]:
paragraphs = chapter_1_json["paragraphs"]

In [6]:
llm = Llama(
    model_path="/home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin",
    n_ctx=4096,
    n_gpu_layers=30
)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 5.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: mem required  = 3773.79 MB (+ 2048.00 MB per state)
llama_new_context_with_mo

In [5]:
def translate_paragraph(text, llm, use_example=None, method=None):
    """
    Translation function that supports Completion and ChatCompletion
    """
    model_path = "/home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin"

    # ChatCompletion
    system_prompt="Translate from Chinese to English, only reply in English 把中文翻译成英文，只用英文回答问题"
    n_ctx = 4096
    llm = Llama(model_path=model_path, n_ctx=n_ctx)

    # message components
    messages = []

    # system prompt
    system_prompt = {"role": "system", "content": system_prompt}
    messages.append(system_prompt)

    # examples to help the completion get a better sense of how to translate
    if use_example:
        messages.append({"role": "user", "content": "在那个已被忘却的日子里，它的世界颠覆了。泥土飞走，出现了一条又深又宽的峡谷，然后泥土又轰隆隆地飞回来，峡谷消失了，在原来峡谷的尽头出现了一座黑色的孤峰。其实，在这片广阔的疆域上，这种事常常发生，泥土飞走又飞回，峡谷出现又消失，然后是孤峰降临，好像是给每次灾变打上一个醒目的标记。褐蚁和几百个同族带着幸存的蚁后向太阳落下的方向走了一段路，建立了新的帝国。"})
        messages.append({"role": "assistant", "content": "In that forgotten day, its world was turned upside down. The soil flew away and a deep and wide canyon appeared, then the soil flew back and the canyon disappeared, at the end of which appeared a black peak. In fact, such things often happened in this vast domain, where the soil flew away and flew back, then there was a canyon, then a peak, as if to mark each disaster. The brown ants and hundreds of their kind with surviving queens walked towards the direction where the sun set and established a new empire."})

    messages.append({"role": "user", "content": text})

    # ChatCompletion
    if method != "completion":
        response = llm.create_chat_completion(
            messages=messages,
            max_tokens=5000,
            model=model_path
        )
        print(response["choices"][0]["message"]["content"])
        return response

    # Completion (simple completion)
    else:
        completion_prompt = f"### Chinese:\n你好\n\n### English:\nHello\n\n### Chinese:\n${text}\n\n### English:\n"
        stop = ["\n","###"]
        response = llm.create_completion(max_tokens=5000,model=model_path, prompt=completion_prompt, stop=stop)
        print(response["choices"][0]["text"])
        return response

In [6]:
tokenizer = LlamaTokenizer(llama=llm)

In [7]:
TEXT="在那个已被忘却的日子里，它的世界颠覆了。泥土飞走，出现了一条又深又宽的峡谷，然后泥土又轰隆隆地飞回来，峡谷消失了，在原来峡谷的尽头出现了一座黑色的孤峰。其实，在这片广阔的疆域上，这种事常常发生，泥土飞走又飞回，峡谷出现又消失，然后是孤峰降临，好像是给每次灾变打上一个醒目的标记。褐蚁和几百个同族带着幸存的蚁后向太阳落下的方向走了一段路，建立了新的帝国。"
tokens = tokenizer.encode(TEXT)

In [8]:
print(str(tokens[:4]) + " ...")

[1, 30505, 32380, 36812] ...


In [9]:
for token in tokens:
    text = tokenizer.decode([token])
    print(text, end=" ")

 在 那个 已被 忘 却 的日子 里 ， 它的 世界 颠覆 了 。 泥 土 飞 走 ， 出现了 一条 又 深 又 宽 的 峡谷 ， 然后 泥 土 又 轰 隆 隆 地 飞 回来 ， 峡谷 消失 了 ， 在 原来 峡谷 的 尽头 出现了 一座 黑色 的 孤 峰 。 其实 ， 在这 片 广阔 的 疆 域 上 ， 这种事 常常 发生 ， 泥 土 飞 走 又 飞 回 ， 峡谷 出现 又 消失 ， 然后 是 孤 峰 降临 ， 好像是 给 每次 灾 变 打 上 一个 醒目 的 标记 。 褐 蚁 和 几百 个 同 族 带着 幸 存 的 蚁 后 向 太阳 落 下的 方向 走了 一段 路 ， 建立了 新的 帝国 。 

In [10]:
translations = []
for paragraph in paragraphs[:2]:
    translation = translate_paragraph(paragraph, llm=llm, method="completion")
    cn_text = translation["choices"][0]["text"]
    p = {}
    p["EN"] = paragraph
    p["CN"] = cn_text
    translations.append(p)

print(translations)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

The word "basement" is a plain one, which can't be very fashionable or exciting, but it conveys our emotion and confidence in constructing the futuristic fantastic skyscraper in China accurately. Therefore, we use it as the name of this original collection.



llama_print_timings:        load time =  2690.92 ms
llama_print_timings:      sample time =    28.63 ms /    65 runs   (    0.44 ms per token,  2270.35 tokens per second)
llama_print_timings: prompt eval time =  2690.61 ms /    75 tokens (   35.87 ms per token,    27.87 tokens per second)
llama_print_timings:        eval time =  5577.53 ms /    64 runs   (   87.15 ms per token,    11.47 tokens per second)
llama_print_timings:       total time =  8392.41 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

In the past ten years, science fiction has developed rapidly. Wang Jiankang, Liu Xiangxin, He Hongwei, and Han Song are just a few of the many science fiction writers who have published many works loved by readers and filled with innovative and exploratory value. The leading journal of science fiction has also gone from one traditional publication, Science Fiction World, to encompassing various levels of readers. At the same time, the market environment for science fiction has improved as major bookstores in provincial capitals have finally created a domain specifically for science fiction literature.



llama_print_timings:        load time =   737.99 ms
llama_print_timings:      sample time =    56.39 ms /   125 runs   (    0.45 ms per token,  2216.67 tokens per second)
llama_print_timings: prompt eval time =   737.95 ms /   129 tokens (    5.72 ms per token,   174.81 tokens per second)
llama_print_timings:        eval time = 10717.76 ms /   124 runs   (   86.43 ms per token,    11.57 tokens per second)
llama_print_timings:       total time = 11704.82 ms


[{'EN': '“基石”是个平实的词，不够“炫”，却能够准确传达我们对构建中的中国科幻繁华巨厦的情感与信心，因此，我们用它来作为这套原创丛书的名字。', 'CN': 'The word "basement" is a plain one, which can\'t be very fashionable or exciting, but it conveys our emotion and confidence in constructing the futuristic fantastic skyscraper in China accurately. Therefore, we use it as the name of this original collection.'}, {'EN': '最近十年，是科幻创作飞速发展的十年。王晋康、刘慈欣、何宏伟、韩松等一大批科幻作家发表了大量深受读者喜爱、极具开拓与探索价值的科幻佳作。科幻文学的龙头期刊更是从一本传统的《科幻世界》，发展壮大成为涵盖各个读者层的系列刊物。与此同时，科幻文学的市场环境也有了改善，省会级城市的大型书店里终于有了属于科幻的领地。', 'CN': 'In the past ten years, science fiction has developed rapidly. Wang Jiankang, Liu Xiangxin, He Hongwei, and Han Song are just a few of the many science fiction writers who have published many works loved by readers and filled with innovative and exploratory value. The leading journal of science fiction has also gone from one traditional publication, Science Fiction World, to encompassing various levels of readers. At the same time, the market environment for science fiction has 

In [12]:
# let's write a function that can add English translations to our file for a given chapter in a book
import json

def translate_chapter(llm, book_path, chapter_number):
    # open the file
    with open(f"../data/books/{book_path}/chapters/{chapter_number}.json", "r") as f:
        chapter = json.loads(f.read())
        translated_paragraphs = []
        for paragraph in chapter["paragraphs"]:
            translated_paragraph = translate_paragraph(paragraph, llm=llm, method="completion")
            translated_paragraphs.append(translated_paragraph["choices"][0]["text"])

        chapter["translated_paragraphs"] = translated_paragraphs

    with open(f"../data/books/{book_path}/chapters/{chapter_number}.json", "w") as f:
        json.dump(chapter, f, ensure_ascii=False)

    print(f"translated {len(translated_paragraphs)}.")

In [48]:
translate_chapter(llm, "three_body", 1)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

The word "basement" is a plain one, which can't be very fashionable or exciting, but it conveys our emotion and confidence in constructing the futuristic fantastic skyscraper in China accurately. Therefore, we use it as the name of this original collection.



llama_print_timings:        load time =   657.11 ms
llama_print_timings:      sample time =    30.00 ms /    65 runs   (    0.46 ms per token,  2166.31 tokens per second)
llama_print_timings: prompt eval time =   657.08 ms /    75 tokens (    8.76 ms per token,   114.14 tokens per second)
llama_print_timings:        eval time =  5626.07 ms /    64 runs   (   87.91 ms per token,    11.38 tokens per second)
llama_print_timings:       total time =  6419.89 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

In the past ten years, science fiction has developed rapidly. Wang Jiankang, Liu Xiangxin, He Hongwei, and Han Song are just a few of the many science fiction writers who have published many works loved by readers and filled with innovative and exploratory value. The leading journal of science fiction has also gone from one traditional publication, Science Fiction World, to encompassing various levels of readers. At the same time, the market environment for science fiction has improved as major bookstores in provincial capitals have finally created a domain specifically for science fiction literature.



llama_print_timings:        load time =   724.70 ms
llama_print_timings:      sample time =    55.76 ms /   125 runs   (    0.45 ms per token,  2241.67 tokens per second)
llama_print_timings: prompt eval time =   724.66 ms /   129 tokens (    5.62 ms per token,   178.02 tokens per second)
llama_print_timings:        eval time = 10869.87 ms /   124 runs   (   87.66 ms per token,    11.41 tokens per second)
llama_print_timings:       total time = 11854.71 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

...


llama_print_timings:        load time =   674.61 ms
llama_print_timings:      sample time =    41.50 ms /    90 runs   (    0.46 ms per token,  2168.78 tokens per second)
llama_print_timings: prompt eval time =   674.56 ms /    99 tokens (    6.81 ms per token,   146.76 tokens per second)
llama_print_timings:        eval time =  7465.91 ms /    89 runs   (   83.89 ms per token,    11.92 tokens per second)
llama_print_timings:       total time =  8331.59 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

That's important to note, because there are no limits on the type of stone you can use for a foundation. Because building a building requires various kinds of stone.



llama_print_timings:        load time =   604.99 ms
llama_print_timings:      sample time =    15.60 ms /    35 runs   (    0.45 ms per token,  2244.17 tokens per second)
llama_print_timings: prompt eval time =   604.95 ms /    56 tokens (   10.80 ms per token,    92.57 tokens per second)
llama_print_timings:        eval time =  2781.95 ms /    34 runs   (   81.82 ms per token,    12.22 tokens per second)
llama_print_timings:       total time =  3458.81 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

We are full of expectation for such a building.
translated 7.



llama_print_timings:        load time =   595.52 ms
llama_print_timings:      sample time =     4.90 ms /    11 runs   (    0.45 ms per token,  2244.44 tokens per second)
llama_print_timings: prompt eval time =   595.48 ms /    50 tokens (   11.91 ms per token,    83.97 tokens per second)
llama_print_timings:        eval time =   835.16 ms /    10 runs   (   83.52 ms per token,    11.97 tokens per second)
llama_print_timings:       total time =  1452.44 ms


In [13]:
translate_chapter(llm, "three_body", 2)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

终于,《三体》可以和科幻朋友们见面了.我们都没有想到,连载的形式出现.之前,就题材问题与编辑们仔细商讨过.看来没有什么大的问题,但没想到今年是文化大革命三十周年纪念,单行本一时无法出版，只能这样。



llama_print_timings:        load time =   721.45 ms
llama_print_timings:      sample time =    41.77 ms /    60 runs   (    0.70 ms per token,  1436.37 tokens per second)
llama_print_timings: prompt eval time =   721.41 ms /    90 tokens (    8.02 ms per token,   124.76 tokens per second)
llama_print_timings:        eval time =  5558.33 ms /    59 runs   (   94.21 ms per token,    10.61 tokens per second)
llama_print_timings:       total time =  6454.68 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

The book is not actually about the Cultural Revolution, but it has a lingering spiritual ghost from the period that only makes up a fraction of its content.



llama_print_timings:        load time =   613.51 ms
llama_print_timings:      sample time =    14.50 ms /    33 runs   (    0.44 ms per token,  2276.18 tokens per second)
llama_print_timings: prompt eval time =   613.47 ms /    59 tokens (   10.40 ms per token,    96.17 tokens per second)
llama_print_timings:        eval time =  2744.67 ms /    32 runs   (   85.77 ms per token,    11.66 tokens per second)
llama_print_timings:       total time =  3419.78 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

...

My friends will see that this first installment is not really a science fiction novel, but this book is not showing the same as it does in this period. It is less science-fiction and more ethereal than Ball Lightning, I hope you can be patient enough to keep going, because the following stories will change greatly.



llama_print_timings:        load time =   655.42 ms
llama_print_timings:      sample time =    31.25 ms /    69 runs   (    0.45 ms per token,  2207.79 tokens per second)
llama_print_timings: prompt eval time =   655.38 ms /    81 tokens (    8.09 ms per token,   123.59 tokens per second)
llama_print_timings:        eval time =  5941.80 ms /    68 runs   (   87.38 ms per token,    11.44 tokens per second)
llama_print_timings:       total time =  6736.04 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

In the coming months, readers will travel through my mental journey of the past year, frankly speaking, I don't know what you will see on this dark and mysterious path. But being able to walk together with sci-fi lovers for so long, I am also grateful.



llama_print_timings:        load time =   659.11 ms
llama_print_timings:      sample time =    27.61 ms /    61 runs   (    0.45 ms per token,  2209.02 tokens per second)
llama_print_timings: prompt eval time =   659.05 ms /    86 tokens (    7.66 ms per token,   130.49 tokens per second)
llama_print_timings:        eval time =  5232.48 ms /    60 runs   (   87.21 ms per token,    11.47 tokens per second)
llama_print_timings:       total time =  6012.74 ms


translated 9.


In [14]:
translate_chapter(llm, "three_body", 3)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

China, 1967.



llama_print_timings:        load time =   611.88 ms
llama_print_timings:      sample time =     4.40 ms /    10 runs   (    0.44 ms per token,  2273.24 tokens per second)
llama_print_timings: prompt eval time =   611.85 ms /    37 tokens (   16.54 ms per token,    60.47 tokens per second)
llama_print_timings:        eval time =   775.21 ms /     9 runs   (   86.13 ms per token,    11.61 tokens per second)
llama_print_timings:       total time =  1408.07 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

The attacks on the headquarters of “Four-Twenty-Eighth Army” by the “Red Unification” lasted for two days. Their flags fluttered around the building like the seeds seeking the fire. The commander of the “Red Unification” was anxious and uneasy, fearing not their defenders, who were only about two hundred and fifteen soldiers of “Four-Twenty-Eighth Army”, but those more than ten large dynamite mines inside the building. He did not see them, but could feel their presence like a magnet, and he knew that if those switches were turned on, they would cause great damage with all their might. However, those young red guards were fierce and crazy, just like wolves gathered around fire ashes. They were very different from the first-generation Red Guards who had matured in the rain and wind.



llama_print_timings:        load time =   926.57 ms
llama_print_timings:      sample time =    88.25 ms /   187 runs   (    0.47 ms per token,  2118.96 tokens per second)
llama_print_timings: prompt eval time =   926.52 ms /   231 tokens (    4.01 ms per token,   249.32 tokens per second)
llama_print_timings:        eval time = 16692.00 ms /   186 runs   (   89.74 ms per token,    11.14 tokens per second)
llama_print_timings:       total time = 18006.76 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

...

She finally found herself in front of the door to her friend Neng's home. During their four years at university, Neng had been her teacher and closest friend, who she spent two years studying as a graduate student in astrophysics. After reading about space exploration, to the present day when the school closed down, Neng had always been her most close person, other than her father. Neng had studied abroad at Cambridge University, his home filled with beautiful European books, paintings and records, a piano; there were also many exquisite pipe tobacco tins on their delicate wooden shelves, each one containing the roots of the Mediterranean sea bamboo or Turkey sea bubble stone, in which Neng's father gave her a pipe that has been soaking up his wisdom. These smoking pipes were like the presence of Neng, who had never mentioned anything about him before, but this small, warm and elegant world was a haven for her to escape the storm in the real world. But that happened before Neng's home 


llama_print_timings:        load time =  1027.13 ms
llama_print_timings:      sample time =   132.17 ms /   292 runs   (    0.45 ms per token,  2209.23 tokens per second)
llama_print_timings: prompt eval time =  1027.10 ms /   277 tokens (    3.71 ms per token,   269.69 tokens per second)
llama_print_timings:        eval time = 25996.31 ms /   291 runs   (   89.33 ms per token,    11.19 tokens per second)
llama_print_timings:       total time = 27620.78 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

叶文洁 opened the door to Neng Wan's house and found that after being ransacked, the messy room had become tidied up. Those damaged paintings that had been tore down were put back on the wall with clean pictured frames, the knocked-down piano also stood erect in its original spot, though it was unable to be played because it had been broken… Neng Wan stood by her writing desk. She touched her forehead, face and hands, all of which were cold. In fact, Ye Wenjie noticed an empty sleeping pill bottle on the writing desk. She stood still for a while, then turned around and left without saying anything, feeling no sadness anymore. She felt like a counter was set to zero when exposed to excessive radiation… However, before she opened the door, she looked back at Neng Wan with a last glance. It was found that Neng teacher had put on lipstick and worn high heels.



llama_print_timings:        load time =  1012.53 ms
llama_print_timings:      sample time =    98.43 ms /   214 runs   (    0.46 ms per token,  2174.13 tokens per second)
llama_print_timings: prompt eval time =  1012.48 ms /   264 tokens (    3.84 ms per token,   260.75 tokens per second)
llama_print_timings:        eval time = 18866.08 ms /   213 runs   (   88.57 ms per token,    11.29 tokens per second)
llama_print_timings:       total time = 20326.80 ms


translated 58.


In [15]:
translate_chapter(llm, "three_body", 4)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

In two years, Great Xing'an Mountain.



llama_print_timings:        load time =   594.99 ms
llama_print_timings:      sample time =     5.73 ms /    12 runs   (    0.48 ms per token,  2092.78 tokens per second)
llama_print_timings: prompt eval time =   594.96 ms /    37 tokens (   16.08 ms per token,    62.19 tokens per second)
llama_print_timings:        eval time =   940.77 ms /    11 runs   (   85.52 ms per token,    11.69 tokens per second)
llama_print_timings:       total time =  1562.59 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

"Sunshine and rain, day and night. "



llama_print_timings:        load time =   589.29 ms
llama_print_timings:      sample time =     6.89 ms /    14 runs   (    0.49 ms per token,  2031.05 tokens per second)
llama_print_timings: prompt eval time =   589.27 ms /    37 tokens (   15.93 ms per token,    62.79 tokens per second)
llama_print_timings:        eval time =  1086.38 ms /    13 runs   (   83.57 ms per token,    11.97 tokens per second)
llama_print_timings:       total time =  1705.74 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

...

She was enveloped in a cloud of ice and then saw a building, from which she could see a girl waving a flag. Her slim frame and the expanse of the flag created an ironic contrast. That was Ye Wenjie's sister Yeyan Shu. Since he separated from his reactionary academic authorities, Ye Wenjie had never heard anything about her since she was brutally murdered in a mass campaign two years ago. In a daze, the flag-waving person changed into Li Baolin, whose glasses reflected the fire below; then again into Cheng Lei, into mother Sholing and even father. The flag-holder kept changing and waving the flag without stopping, like a eternal pendulum counting down Ye Wenjie's remaining life.



llama_print_timings:        load time =   840.66 ms
llama_print_timings:      sample time =    78.04 ms /   174 runs   (    0.45 ms per token,  2229.57 tokens per second)
llama_print_timings: prompt eval time =   840.62 ms /   187 tokens (    4.50 ms per token,   222.46 tokens per second)
llama_print_timings:        eval time = 15205.47 ms /   173 runs   (   87.89 ms per token,    11.38 tokens per second)
llama_print_timings:       total time = 16406.74 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

The flag faded, everything faded, and that piece of universe-filled ice wrapped her up again, this time in black.



llama_print_timings:        load time =   627.26 ms
llama_print_timings:      sample time =    12.54 ms /    28 runs   (    0.45 ms per token,  2232.32 tokens per second)
llama_print_timings: prompt eval time =   627.23 ms /    60 tokens (   10.45 ms per token,    95.66 tokens per second)
llama_print_timings:        eval time =  2396.51 ms /    27 runs   (   88.76 ms per token,    11.27 tokens per second)
llama_print_timings:       total time =  3079.12 ms


translated 102.


In [ ]:
translate_chapter(llm, "three_body", 5)

In [ ]:
translate_chapter(llm, "three_body", 6)

In [18]:
for i in range(5, 37):
    translate_chapter(llm, "three_body", i)

llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

She had been in darkness for so long that she couldn't tell if it had only been a few moments or several days. The heavy crashing sounds reverberated from every direction, as though there were some immense mechanical gadgets digging under her very core of being. Despite the darkness, the sound seemed to become more and more real, and she finally realized that the source was not heaven nor hell. She made an effort to open her eyelids, which felt heavy as stones……First, she saw a lamp deep embedded within the ceiling, surrounded by iron mesh to protect it from impacts. It emitted dim light, and the ceiling seemed to be made of metal.



llama_print_timings:        load time =   840.15 ms
llama_print_timings:      sample time =    70.76 ms /   145 runs   (    0.49 ms per token,  2049.27 tokens per second)
llama_print_timings: prompt eval time =   840.11 ms /   170 tokens (    4.94 ms per token,   202.35 tokens per second)
llama_print_timings:        eval time = 12852.83 ms /   144 runs   (   89.26 ms per token,    11.20 tokens per second)
llama_print_timings:       total time = 14007.36 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

She heard a male voice calling her name softly.



llama_print_timings:        load time =   588.15 ms
llama_print_timings:      sample time =     5.93 ms /    12 runs   (    0.49 ms per token,  2023.61 tokens per second)
llama_print_timings: prompt eval time =   588.13 ms /    40 tokens (   14.70 ms per token,    68.01 tokens per second)
llama_print_timings:        eval time =   925.84 ms /    11 runs   (   84.17 ms per token,    11.88 tokens per second)
llama_print_timings:       total time =  1540.07 ms
llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_inte

...

Oh, and finally, thank you all!


llama.cpp: loading model from /home/brian/github/llama.cpp/models/7B/Chinese-Alpaca-2/ggml-model-q4_0.bin
llama_model_load_internal: format     = ggjt v3 (latest)
llama_model_load_internal: n_vocab    = 55296
llama_model_load_internal: n_ctx      = 4096
llama_model_load_internal: n_embd     = 4096
llama_model_load_internal: n_mult     = 5504
llama_model_load_internal: n_head     = 32
llama_model_load_internal: n_head_kv  = 32
llama_model_load_internal: n_layer    = 32
llama_model_load_internal: n_rot      = 128
llama_model_load_internal: n_gqa      = 1
llama_model_load_internal: rnorm_eps  = 1.0e-06
llama_model_load_internal: n_ff       = 11008
llama_model_load_internal: freq_base  = 10000.0
llama_model_load_internal: freq_scale = 1
llama_model_load_internal: ftype      = 2 (mostly Q4_0)
llama_model_load_internal: model size = 7B
llama_model_load_internal: ggml ctx size =    0.08 MB
llama_model_load_internal: using CUDA for GPU acceleration
llama_model_load_internal: mem required  = 42

Luo Cixin



llama_print_timings:        load time =   567.03 ms
llama_print_timings:      sample time =     2.75 ms /     6 runs   (    0.46 ms per token,  2181.82 tokens per second)
llama_print_timings: prompt eval time =   566.99 ms /    32 tokens (   17.72 ms per token,    56.44 tokens per second)
llama_print_timings:        eval time =   428.42 ms /     5 runs   (   85.68 ms per token,    11.67 tokens per second)
llama_print_timings:       total time =  1006.98 ms


translated 13.


In [ ]:
for i in range (1,51):
    print("################")
    translate_chapter(llm, "dark_forest", i)
# took 446 minutes

In [ ]:
for i in range (1,59):
    print("################")
    translate_chapter(llm, "deaths_end", i)